# flox: Faster GroupBy aggregations with Xarray

**Authors** Deepak Cherian, Kevin Sampson, Matthew Rocklin

Significantly faster groupby calculations are now possible through a new-ish package in the Xarray/Dask/Pangeo ecosystem called [flox](https://flox.readthedocs.io/en/latest/). Practically, this means faster climatologies, faster resampling, faster histogramming, and faster compositing of array datasets.


## The National Water Model Dataset


To show off, we demonstrate county-wise aggregation of output from the National Water Model (NWM) available on the [AWS Public Data Registry](https://registry.opendata.aws/nwm-archive/).


Quoting [the NOAA page](https://water.noaa.gov/about/nwm) for more.

> The National Water Model (NWM) is a hydrologic modelling framework that simulates observed and forecast streamflow over the entire continental United States (CONUS). The NWM simulates the water cycle with mathematical representations of the different processes and how they fit together. This complex representation of physical processes such as snowmelt and infiltration and movement of water through the soil layers varies significantly with changing elevations, soils, vegetation types and a host of other variables. Additionally, extreme variability in precipitation over short distances and times can cause the response on rivers and streams to change very quickly. Overall, the process is so complex that to simulate it with a mathematical model means that it needs a very high powered computer or supercomputer in order to run in the time frame needed to support decision makers when flooding is threatened.  

> All CONUS model configurations provide streamflow for 2.7 million river reaches and other hydrologic information on 1km and 250m grids.



## Problem description

We want to calculate county-level means for 3 hourly time series data on the 250m grid. This is a *Groupby* problem. 

GroupBy is a term used for a very common analysis pattern commonly called "split-apply-combine" ([Wickham, 2011](https://www.jstatsoft.org/article/view/v040i01)) wherein an analyst 
- *Splits* a dataset into groups (e.g. counties),
- *Applies* a transformation to each group of data (here a reduction like `.mean`)
- *Combines* the results of `apply` to form a new dataset


For this problem we will split the dataset into counties, apply the `mean`, and then combine the results back.

With [Xarray](https://docs.xarray.dev/en/stable/user-guide/groupby.html), this would look like
```python
dataset.groupby(counties).mean()
```

However Xarray's default algorithm is a simple for-loop over groups and doesn't work very well for large distributed problems.

## Enter `flox`.

`flox` solves a long-standing problem in the Pangeo array computing ecosytem of computing GroupBy reductions. It implements a parallel groupby algorithm (using a tree reduction) to substantially improve performance of groupby reductions with dask. 
  - Specifically, `flox` speeds up [reduction methods](https://flox.readthedocs.io/en/latest/aggregations.html) like `groupby(...).mean()`, `groupby(...).max()`, etc, but not `groupby.map`.
  - `flox` also significantly speeds up groupby reductions with pure numpy arrays using optimized implementations in the [`numpy-groupies` package](https://github.com/ml31415/numpy-groupies).
  - `flox` allows more complicated groupby operations such as lazy grouping by a dask array, and grouping by multiple variables. Use `flox.xarray.xarray_reduce` for [these operations](https://flox.readthedocs.io/en/latest/xarray.html). Xarray currently only supports grouping by a single numpy variable.

See [here](https://flox.readthedocs.io/en/latest/intro.html) for short examples.

### How do I use it?

Run `mamba install flox` and `xarray>=2022.06.0` will use it by default for `.groupby`, `.groupby_bins`, and `.resample`!

A lot of effort was spent in ensuring backwards compatibility, so your workloads should only work better. Let us know if it [does not](https://github.com/pydata/xarray/issues)


## Setup cluster with Coiled

To demonstrate calculation on a cloud-available dataset, we will use [Coiled](https://coiled.io) to set up a dask cluster in AWS `us-east-1`.

In [60]:
import coiled

cluster = coiled.Cluster(
    region="us-east-1",
    n_workers=10,
    tags={"project": "nwm"},
    scheduler_vm_types="r7g.large",
    worker_vm_types="c7g.xlarge"
)

client = cluster.get_client()

cluster.adapt(minimum=10, maximum=40)

Output()

Output()

2023-07-24 16:53:35,865 - distributed.deploy.adaptive - INFO - Adaptive scaling started: minimum=10 maximum=40


## Setup

In [61]:
%load_ext watermark

import flox  # make sure its available
import fsspec
import numpy as np
import rioxarray
import xarray as xr

xr.set_options(
    display_expand_attrs=False,
    display_expand_coords=False,
    display_expand_data=True,
)

%watermark -iv

The watermark extension is already loaded. To reload it, use:
  %reload_ext watermark
rioxarray: 0.14.1
geopandas: 0.13.2
xarray   : 2023.7.0
flox     : 0.7.2
hvplot   : 0.8.4
fsspec   : 2023.6.0
numpy    : 1.24.4
coiled   : 0.8.14



## Load NWM data

In [62]:
ds = xr.open_zarr(
    fsspec.get_mapper("s3://noaa-nwm-retrospective-2-1-zarr-pds/rtout.zarr", anon=True),
    consolidated=True,
)
ds

<xarray.Dataset>
Dimensions:       (time: 122479, y: 15360, x: 18432)
Coordinates: (3)
Data variables:
    crs           |S1 ...
    sfcheadsubrt  (time, y, x) float64 dask.array<chunksize=(224, 350, 350), meta=np.ndarray>
    zwattablrt    (time, y, x) float64 dask.array<chunksize=(224, 350, 350), meta=np.ndarray>
Attributes: (7)

Each field in this dataset is big!

In [63]:
ds.zwattablrt

<xarray.DataArray 'zwattablrt' (time: 122479, y: 15360, x: 18432)>
dask.array<open_dataset-zwattablrt, shape=(122479, 15360, 18432), dtype=float64, chunksize=(224, 350, 350), chunktype=numpy.ndarray>
Coordinates: (3)
Attributes: (4)

We'll subset to a single year subset for demo purposes

In [64]:
# subset = ds.zwattablrt.sel(time=slice("2001-01-01", "2020-12-31"))
subset = ds.zwattablrt.sel(time=slice("2001-01-01", "2002-12-31"))
subset

<xarray.DataArray 'zwattablrt' (time: 5840, y: 15360, x: 18432)>
dask.array<getitem, shape=(5840, 15360, 18432), dtype=float64, chunksize=(224, 350, 350), chunktype=numpy.ndarray>
Coordinates: (3)
Attributes: (4)

## Load county raster for grouping

A raster TIFF file identifying counties by a unique integer was created separately and saved. 

We load that using [rioxarray](https://corteva.github.io/rioxarray/html/rioxarray.html)

In [65]:
import fsspec
import rioxarray

fs = fsspec.filesystem("s3", requester_pays=True)

counties = rioxarray.open_rasterio(
    fs.open("s3://nwm-250m-us-counties/Counties_on_250m_grid.tif"), chunks="auto"
).squeeze()
counties

# remove any small floating point error in coordinate locations
_, counties_aligned = xr.align(ds, counties, join="override")

counties_aligned

<xarray.DataArray (y: 15360, x: 18432)>
dask.array<getitem, shape=(15360, 18432), dtype=int32, chunksize=(1820, 18432), chunktype=numpy.ndarray>
Coordinates: (4)
Attributes: (9)

We'll need the unique county IDs later, calculate that now.

In [66]:
county_id = np.unique(counties_aligned.data).compute()
county_id = county_id[county_id != 0]
print(f"There are {len(county_id)} counties!")

There are 3108 counties!


## GroupBy with flox

We could run the computation as

```python
subset.groupby(counties_aligned).mean()
```

This would use flox in the background.

However it would also load `counties_aligned` in to memory (an unfortunate Xarray implementation detail) which is not so bad (only a gig). To avoid egress charges, we'll instead go through `flox.xarray` which allows you to lazily groupby a dask array (here `counties_aligned`) as long as you pass in the expected group labels in `expected_groups`.

See [here](https://flox.readthedocs.io/en/latest/intro.html#with-dask) for more.

In [67]:
import flox.xarray

county_mean = flox.xarray.xarray_reduce(
    subset,
    counties_aligned.rename("county"),
    func="mean",
    expected_groups=(county_id,),
)

county_mean

<xarray.DataArray 'zwattablrt' (time: 5840, county: 3108)>
dask.array<groupby_nanmean, shape=(5840, 3108), dtype=float64, chunksize=(224, 3108), chunktype=numpy.ndarray>
Coordinates: (4)
Attributes: (4)

In [69]:
county_mean.load()

<xarray.DataArray 'zwattablrt' (time: 5840, county: 3108)>
array([[1.77092178, 1.79430538, 1.71125074, ..., 1.97485099, 1.90160141,
        1.86238405],
       [1.77233924, 1.79459704, 1.71276979, ..., 1.97483864, 1.90030852,
        1.86265516],
       [1.77146351, 1.7946418 , 1.71316782, ..., 1.97485716, 1.89992493,
        1.8630656 ],
       ...,
       [1.61900536, 1.52626702, 1.57021746, ..., 1.97238484, 1.97396421,
        1.7895197 ],
       [1.62087494, 1.52687923, 1.57316078, ..., 1.97244408, 1.97397461,
        1.78901529],
       [1.62212947, 1.52734704, 1.57211559, ..., 1.97233917, 1.97405087,
        1.78848819]])
Coordinates: (4)
Attributes: (4)

The computation proceeds very nicely. 

We don't anticipate trouble scaling this computation up to the full dataset.

## Cleanup

In [70]:
cluster.shutdown()

2023-07-24 17:07:14,719 - distributed.deploy.adaptive_core - INFO - Adaptive stop
2023-07-24 17:07:16,200 - distributed.deploy.adaptive_core - INFO - Adaptive stop


In [84]:
county_mean.to_netcdf("mean_zwattablrt_nwm.nc")

In [88]:
county_mean = xr.open_dataset("mean_zwattablrt_nwm.nc")

## Visualize yearly mean

Read county shapefile, combo of state FIPS code and county FIPS code as multi-index

In [89]:
import geopandas as gpd
import hvplot.pandas

counties = gpd.read_file(
    "https://www2.census.gov/geo/tiger/GENZ2022/shp/cb_2022_us_county_20m.zip"
).to_crs("EPSG:3395")
counties["STATEFP"] = counties.STATEFP.astype(int)
counties["COUNTYFP"] = counties.COUNTYFP.astype(int)
continental = counties.loc[~counties["STATEFP"].isin([2, 15, 72])]
continental = continental.set_index(["STATEFP", "COUNTYFP"])

Interpret `county` as combo of state FIPS code and county FIPS code. Set multi-index

In [90]:
yearly_mean = county_mean.mean("time")
yearly_mean.coords["STATEFP"] = (yearly_mean.county // 1000).astype(int)
yearly_mean.coords["COUNTYFP"] = np.mod(yearly_mean.county, 1000).astype(int)
yearly_mean = yearly_mean.drop_vars("county").set_index(county=["STATEFP", "COUNTYFP"])
yearly_mean

<xarray.Dataset>
Dimensions:      (county: 3108)
Coordinates: (5)
Data variables:
    zwattablrt   (county) float64 1.682 1.507 1.427 1.594 ... 1.976 1.941 1.887

Join

In [91]:
continental["zwattablrt"] = yearly_mean.to_dataframe()["zwattablrt"]

In [92]:
continental

COUNTYNS        AFFGEOID  GEOID       NAME  \
STATEFP COUNTYFP                                               
17      127       01784730  0500000US17127  17127     Massac   
27      17        00659454  0500000US27017  27017    Carlton   
37      181       01008591  0500000US37181  37181      Vance   
47      79        01639755  0500000US47079  47079      Henry   
6       21        00277275  0500000US06021  06021      Glenn   
...                    ...             ...    ...        ...   
51      167       01497573  0500000US51167  51167    Russell   
40      89        01101835  0500000US40089  40089  McCurtain   
1       105       00161579  0500000US01105  01105      Perry   
54      43        01550028  0500000US54043  54043    Lincoln   
17      125       00424261  0500000US17125  17125      Mason   

                          NAMELSAD STUSPS      STATE_NAME LSAD       ALAND  \
STATEFP COUNTYFP                                                             
17      127          Massac County     IL        Illinois   06   614218330   
27      17          Carlton County     MN       Minnesota   06  2230473967   
37      181           Vance County     NC  North Carolina   06   653701481   
47      79            Henry County     TN       Tennessee   06  1455320362   
6       21            Glenn County     CA      California   06  3403160299   
...                            ...    ...             ...  ...         ...   
51      167         Russell County     VA        Virginia   06  1226421378   
40      89        McCurtain County     OK        Oklahoma   06  4793496603   
1       105           Perry County     AL         Alabama   06  1863936201   
54      43          Lincoln County     WV   West Virginia   06  1132065764   
17      125           Mason County     IL        Illinois   06  1396914848   

                     AWATER  \
STATEFP COUNTYFP              
17      127        12784614   
27      17         36173451   
37      181        42190675   
47      79         81582236   
6       21         33693344   
...                     ...   
51      167         7558481   
40      89        133942698   
1       105        10902207   
54      43          4053564   
17      125        62748513   

                                                           geometry  \
STATEFP COUNTYFP                                                      
17      127       POLYGON ((-9899503.889 4455506.800, -9896867.1...   
27      17        POLYGON ((-10359540.224 5872907.231, -10274975...   
37      181       POLYGON ((-8738332.957 4346219.160, -8733823.9...   
47      79        POLYGON ((-9853595.905 4344424.296, -9853101.8...   
6       21        POLYGON ((-13682478.726 4809490.889, -13586151...   
...                                                             ...   
51      167       POLYGON ((-9173464.253 4396242.834, -9161437.6...   
40      89        POLYGON ((-10592775.814 4025907.915, -10592197...   
1       105       POLYGON ((-9743260.401 3826639.779, -9737551.6...   
54      43        POLYGON ((-9149606.558 4559633.726, -9159736.8...   
17      125       POLYGON ((-10058219.709 4856467.246, -10041702...   

                  zwattablrt  
STATEFP COUNTYFP              
17      127         1.327917  
27      17          0.989152  
37      181         1.615570  
47      79          2.000000  
6       21          1.927344  
...                      ...  
51      167         1.353288  
40      89          1.585679  
1       105         1.079257  
54      43          1.181518  
17      125         1.235083  

[3109 rows x 12 columns]

Plot

In [93]:
continental.hvplot(c="zwattablrt")

:Polygons   [x,y]   (zwattablrt)

In [94]:
continental.hvplot(
    c="zwattablrt",
    cmap='turbo_r',
    title="Average Water Table Depth in 2001 by US County (meters)",
    xaxis=None,
    yaxis=None
)

:Polygons   [x,y]   (zwattablrt)

## Summary

[flox](https://flox.readthedocs.io) makes many large Groupby problems tractable! Use it.


[flox](https://flox.readthedocs.io) also makes many small but more complicated (e.g. multiple variables) Groupby problems tractable! Use it.

We [anticipate](https://github.com/pydata/xarray/issues/6610) upgrading Xarray's interface to enable more complicated GroupBy computations. In the mean time, use flox!